In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

print('Libraries imported.')

Libraries imported.


In [2]:
pip install folium

Note: you may need to restart the kernel to use updated packages.


In [3]:
import folium

### Download the Dataset

In [4]:
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
print('Data downloaded!')

Data downloaded!


In [5]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [6]:
neighborhoods_data = newyork_data['features']

### Convert into a Dataframe

In [7]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

In [8]:
# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [9]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [10]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


### Find all Venues on Foursquare

In [11]:
CLIENT_ID = 'HW5RDJ5EB4ON0JKE2OKJJ0DNZMVJ50RL3H0WI0XL2B5PYXAF' # your Foursquare ID
CLIENT_SECRET = '1UDQW01HU1PYDHWFJXTOC4O5YILARWS0YF2CHCAJDASFXLN4' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: HW5RDJ5EB4ON0JKE2OKJJ0DNZMVJ50RL3H0WI0XL2B5PYXAF
CLIENT_SECRET:1UDQW01HU1PYDHWFJXTOC4O5YILARWS0YF2CHCAJDASFXLN4


In [12]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [13]:
venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude'])

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [14]:
venues.head()

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0     Wakefield               40.894705               -73.847201   
1     Wakefield               40.894705               -73.847201   
2     Wakefield               40.894705               -73.847201   
3     Wakefield               40.894705               -73.847201   
4     Wakefield               40.894705               -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2         Walgreens       40.896528       -73.844700        Pharmacy  
3  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
4           Dunkin'       40.890459       -73.849089      Donut Shop

## Analyze Each Neighborhood

In [15]:
# one hot encoding
ny_onehot = pd.get_dummies(venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
ny_onehot['Neighbourhood'] = venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
ny_onehot = ny_onehot[fixed_columns]

ny_onehot.head()

Neighbourhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Wakefield                  0               0                  0   
1     Wakefield                  0               0                  0   
2     Wakefield                  0               0                  0   
3     Wakefield                  0               0                  0   
4     Wakefield                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                   0                 0                    0             0   
1                   0                 0                    0             0   
2                   0                 0                    0             0   
3                   0                 0                    0             0   
4                   0                 0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Garage  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0                0          0           0           0       0   
1            0                0          0           0           0       0   
2            0                0          0           0           0       0   
3            0                0          0           0           0       0   
4            0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  Bath House  \
0     0    0               0                 0                 0           0   
1     0    0               0                 0                 0           0   
2     0    0               0                 0                 0           0   
3     0    0               0                 0                 0           0   
4     0    0               0                 0                 0           0   

   Beach  Beach Bar  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0      0          0         0            0           0              0   
1      0          0         0            0           0              0   
2      0          0         0            0           0              0   
3      0          0         0            0           0              0   
4      0          0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0      

### Group neighborhoods by occurence of each category

In [16]:
ny_grouped = ny_onehot.groupby('Neighbourhood').mean().reset_index()
ny_grouped

Neighbourhood  Accessories Store  Adult Boutique  \
0                     Allerton           0.000000            0.00   
1                     Annadale           0.000000            0.00   
2                Arden Heights           0.000000            0.00   
3                    Arlington           0.000000            0.00   
4                     Arrochar           0.000000            0.00   
5                      Arverne           0.000000            0.00   
6                      Astoria           0.000000            0.00   
7              Astoria Heights           0.000000            0.00   
8                   Auburndale           0.000000            0.00   
9                   Bath Beach           0.000000            0.00   
10           Battery Park City           0.000000            0.00   
11                   Bay Ridge           0.000000            0.00   
12                 Bay Terrace           0.021277            0.00   
13                  Baychester           0.000000            0.00   
14                     Bayside           0.000000            0.00   
15                   Bayswater           0.000000            0.00   
16                Bedford Park           0.000000            0.00   
17          Bedford Stuyvesant           0.000000            0.00   
18                  Beechhurst           0.000000            0.00   
19                    Bellaire           0.000000            0.00   
20                Belle Harbor           0.000000            0.00   
21                   Bellerose           0.000000            0.00   
22                     Belmont           0.000000            0.00   
23                 Bensonhurst           0.000000            0.00   
24                Bergen Beach           0.000000            0.00   
25                  Blissville           0.000000            0.00   
26                  Bloomfield           0.000000            0.00   
27                 Boerum Hill           0.000000            0.00   
28                Borough Park           0.000000            0.00   
29                Breezy Point           0.000000            0.00   
30                   Briarwood           0.000000            0.00   
31              Brighton Beach           0.000000            0.00   
32               Broad Channel           0.000000            0.00   
33           Broadway Junction           0.000000            0.00   
34                   Bronxdale           0.000000            0.00   
35            Brooklyn Heights           0.000000            0.00   
36                  Brookville           0.000000            0.00   
37                 Brownsville           0.000000            0.00   
38                  Bulls Head           0.000000            0.00   
39                    Bushwick           0.000000            0.00   
40                Butler Manor           0.000000            0.00   
41             Cambria Heights           0.000000            0.00   
42                    Canarsie           0.000000            0.00   
43               Carnegie Hill           0.000000            0.00   
44             Carroll Gardens           0.000000            0.00   
45                 Castle Hill           0.000000            0.00   
46           Castleton Corners           0.000000            0.00   
47              Central Harlem           0.000000            0.00   
48                  Charleston           0.000000            0.00   
49                     Chelsea           0.000000            0.00   
50                   Chinatown           0.000000            0.00   
51                 City Island           0.000000            0.00   
52                   City Line           0.000000            0.00   
53                Civic Center           0.000000            0.00   
54           Claremont Village           0.000000            0.00   
55                Clason Point           0.000000            0.00   
56                     Clifton           0.000000            0.00   
57             

### Display the top ten venues for each neighborhood

In [17]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [18]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighbourhood'] = ny_grouped['Neighbourhood']

for ind in np.arange(ny_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(ny_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place    Chinese Restaurant   
1       Annadale   American Restaurant           Pizza Place   
2  Arden Heights         Deli / Bodega              Pharmacy   
3      Arlington         Deli / Bodega           Coffee Shop   
4       Arrochar              Bus Stop         Deli / Bodega   

  3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
0         Deli / Bodega                   Spa            Supermarket   
1                 Diner         Deli / Bodega           Dance Studio   
2           Coffee Shop              Bus Stop            Pizza Place   
3              Bus Stop          Home Service          Boat or Ferry   
4    Italian Restaurant        Sandwich Place  Outdoors & Recreation   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0   Fried Chicken Joint            Donut Shop                Bakery   
1                  Food            Restaurant                  Park   
2           Flea Market    Falafel Restaurant                  Farm   
3         Grocery Store           Flower Shop                  Farm   
4            Bagel Shop           Pizza Place    Athletics & Sports   

  9th Most Common Venue 10th Most Common Venue  
0              Pharmacy      Electronics Store  
1         Train Station                  Field  
2        Farmers Market   Fast Food Restaurant  
3        Farmers Market   Fast Food Restaurant  
4                 Hotel      Polish Restaurant

In [19]:
# set number of clusters
kclusters = 10

ny_clustering = ny_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ny_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 3, 0, 0, 0, 9, 9, 9, 9, 9], dtype=int32)

In [20]:
neighborhoods = neighborhoods.rename(columns = {'Neighborhood':'Neighbourhood'})

In [21]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

In [22]:
ny_merged = neighborhoods.join(neighborhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')
ny_merged.head() # check the last columns! 

Borough Neighbourhood   Latitude  Longitude  Cluster Labels  \
0   Bronx     Wakefield  40.894705 -73.847201               1   
1   Bronx    Co-op City  40.874294 -73.829939               1   
2   Bronx   Eastchester  40.887556 -73.827806               1   
3   Bronx     Fieldston  40.895437 -73.905643               9   
4   Bronx     Riverdale  40.890834 -73.912585               9   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy         Deli / Bodega           Gas Station   
1           Bus Station     Accessories Store           Pizza Place   
2           Bus Station  Caribbean Restaurant         Deli / Bodega   
3  Medical Supply Store                 River                 Plaza   
4                  Park            Food Truck                   Gym   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0        Sandwich Place          Dessert Shop            Donut Shop   
1         Grocery Store  Fast Food Restaurant    Chinese Restaurant   
2                 Diner        Cosmetics Shop  Fast Food Restaurant   
3           Fish Market               Exhibit            Eye Doctor   
4          Home Service         Moving Target                 Plaza   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0        Ice Cream Shop            Laundromat           Yoga Studio   
1                  Park                   Bar            Bagel Shop   
2    Seafood Restaurant    Chinese Restaurant       Automotive Shop   
3               Factory    Falafel Restaurant                  Farm   
4                  Bank           Bus Station            Playground   

  10th Most Common Venue  
0                  Field  
1                  Trail  
2          Bowling Alley  
3         Farmers Market  
4         Farmers Market

In [23]:
address = 'New York, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinates of NY are {}, {}.'.format(latitude, longitude))

The geograpical coordinates of NY are 40.7127281, -74.0060152.


### Visualize the clusters

In [24]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(ny_merged['Latitude'], ny_merged['Longitude'], ny_merged['Neighbourhood'], ny_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Examine the Clusters

In [25]:
ny_merged.loc[ny_merged['Cluster Labels'] == 0, ny_merged.columns[[0,1] + list(range(5, ny_merged.shape[1]))]]

Borough     Neighbourhood 1st Most Common Venue  \
45           Bronx          Edenwald         Grocery Store   
89        Brooklyn        Ocean Hill         Deli / Bodega   
150         Queens        Whitestone          Dance Studio   
159         Queens         Briarwood         Deli / Bodega   
193         Queens        Brookville      Recording Studio   
198  Staten Island      New Brighton              Bus Stop   
202  Staten Island       Grymes Hill               Dog Run   
204  Staten Island       South Beach                  Pier   
205  Staten Island     Port Richmond              Bus Stop   
206  Staten Island  Mariner's Harbor         Deli / Bodega   
217  Staten Island       Tottenville        Sandwich Place   
218  Staten Island     Tompkinsville         Deli / Bodega   
224  Staten Island         Park Hill              Bus Stop   
227  Staten Island         Arlington         Deli / Bodega   
228  Staten Island          Arrochar              Bus Stop   
229  Staten Island          Grasmere              Bus Stop   
234  Staten Island    New Dorp Beach    Italian Restaurant   
241  Staten Island     Arden Heights         Deli / Bodega   
245  Staten Island        Bloomfield     Recreation Center   
252  Staten Island       Shore Acres    Italian Restaurant   
254  Staten Island           Concord         Grocery Store   
256  Staten Island     Randall Manor            Playground   
258  Staten Island          Elm Park         Deli / Bodega   
285  Staten Island       Willowbrook    Chinese Restaurant   
305  Staten Island         Fox Hills         Grocery Store   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
45          Deli / Bodega           Supermarket    Chinese Restaurant   
89               Bus Stop         Grocery Store           Supermarket   
150         Deli / Bodega       Bubble Tea Shop           Candy Store   
159                   Gym           Bus Station           Coffee Shop   
193         Deli / Bodega           Yoga Studio           Flower Shop   
198         Deli / Bodega                  Park            Playground   
202         Deli / Bodega     Food & Drink Shop    Falafel Restaurant   
204         Deli / Bodega                 Beach    Athletics & Sports   
205            Donut Shop           Pizza Place            Food Truck   
206    Italian Restaurant    Athletics & Sports           Supermarket   
217         Deli / Bodega    Italian Restaurant    Mexican Restaurant   
218                  Park              Bus Stop               Brewery   
224  Gym / Fitness Center           Coffee Shop                 Hotel   
227           Coffee Shop              Bus Stop          Home Service   
228         Deli / Bodega    Italian Restaurant        Sandwich Place   
229           Pizza Place            Bagel Shop                  Bank   
234         Deli / Bodega                 Beach            Restaurant   
241              Pharmacy           Coffee Shop              Bus Stop   
245          Burger Joint              Bus Stop            Theme Park   
252              Bus Stop         Deli / Bodega          Intersection   
254         Deli / Bodega    Italian Restaurant   Peruvian Restaurant   
256          Neighborhood            Bagel Shop              Bus Stop   
258              Bus Stop    Italian Restaurant        Ice Cream Shop   
285         Deli / Bodega            Bagel Shop          Intersection   
305    African Restaurant              Bus Stop            Playground   

               5th Most Common Venue 6th Most Common Venue  \
45                        Playground           Yoga Studio   
89   Southern / Soul Food Restaurant   Fried Chicken Joint   
150                Food & Drink Shop                  Farm   
159                Convenience Store          Home Service   
193                          Factory    Falafel Restaurant   
198                   Discount Store         Bowling Alley   
202                             Farm        Farmers Market   
204

In [26]:
ny_merged.loc[ny_merged['Cluster Labels'] == 1, ny_merged.columns[[0,1] + list(range(5, ny_merged.shape[1]))]]

Borough        Neighbourhood      1st Most Common Venue  \
0            Bronx            Wakefield                   Pharmacy   
1            Bronx           Co-op City                Bus Station   
2            Bronx          Eastchester                Bus Station   
9            Bronx       Williamsbridge                        Bar   
18           Bronx           West Farms                Bus Station   
19           Bronx         High  Bridge                Bus Station   
23           Bronx             Longwood                 Donut Shop   
25           Bronx           Morrisania                Bus Station   
26           Bronx            Soundview         Chinese Restaurant   
41           Bronx            Olinville              Deli / Bodega   
43           Bronx            Concourse              Grocery Store   
44           Bronx            Unionport                 Donut Shop   
56        Brooklyn        East Flatbush              Moving Target   
71        Brooklyn        Cypress Hills  Latin American Restaurant   
72        Brooklyn        East New York              Deli / Bodega   
73        Brooklyn        Starrett City                Pizza Place   
74        Brooklyn             Canarsie                        Gym   
75        Brooklyn            Flatlands       Caribbean Restaurant   
93        Brooklyn  Prospect Park South       Caribbean Restaurant   
141         Queens        East Elmhurst                 Donut Shop   
158         Queens        Fresh Meadows                Bus Station   
164         Queens        South Jamaica                Bus Station   
165         Queens           St. Albans       Caribbean Restaurant   
166         Queens             Rochdale                     Market   
167         Queens  Springfield Gardens                Bus Station   
168         Queens      Cambria Heights       Caribbean Restaurant   
169         Queens             Rosedale          Accessories Store   
182         Queens           Holliswood                 Donut Shop   
188         Queens            Laurelton       Caribbean Restaurant   
222       Brooklyn              Wingate        Fried Chicken Joint   
223       Brooklyn                Rugby       Caribbean Restaurant   
226  Staten Island         Graniteville              Boat or Ferry   
259       Brooklyn       Remsen Village       Caribbean Restaurant   
263         Queens        Jamaica Hills          Indian Restaurant   
267          Bronx    Claremont Village              Grocery Store   
278         Queens           Blissville              Deli / Bodega   
282       Brooklyn    Broadway Junction                 Donut Shop   
300       Brooklyn              Erasmus       Caribbean Restaurant   

               2nd Most Common Venue      3rd Most Common Venue  \
0                      Deli / Bodega                Gas Station   
1                  Accessories Store                Pizza Place   
2               Caribbean Restaurant              Deli / Bodega   
9                         Soup Place       Caribbean Restaurant   
18                          Bus Stop         Chinese Restaurant   
19                          Pharmacy  Latin American Restaurant   
23              Fast Food Restaurant              Grocery Store   
25                        Donut Shop       Fast Food Restaurant   
26                     Grocery Store               Burger Joint   
41              Caribbean Restaurant          Convenience Store   
43                     Deli / Bodega        Fried Chicken Joint   
44         Latin American Restaurant             Ice Cream Shop   
56                  Department Store                  Wine Shop   
71                        Donut Shop       Fast Food Restaurant   
72                 Convenience Store              Event Service   
73                        Donut Shop       Caribbean Restaurant   
74                  Asian Restaurant            Thai Restaurant   
75                          Pharmacy        Fried Chicken Joint   
93     

In [27]:
ny_merged.loc[ny_merged['Cluster Labels'] == 2, ny_merged.columns[[0,1] + list(range(5, ny_merged.shape[1]))]]

Borough Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
76        Brooklyn   Mill Island                  Pool           Yoga Studio   
238  Staten Island  Butler Manor                  Pool        Baseball Field   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
76             Eye Doctor               Factory    Falafel Restaurant   
238                  Food               Factory    Falafel Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
76                   Farm        Farmers Market  Fast Food Restaurant   
238                  Farm        Farmers Market  Fast Food Restaurant   

    9th Most Common Venue 10th Most Common Venue  
76                  Field    Filipino Restaurant  
238                 Field    Filipino Restaurant

In [28]:
ny_merged.loc[ny_merged['Cluster Labels'] == 3, ny_merged.columns[[0,1] + list(range(5, ny_merged.shape[1]))]]

Borough         Neighbourhood    1st Most Common Venue  \
5            Bronx           Kingsbridge              Pizza Place   
6        Manhattan           Marble Hill           Discount Store   
7            Bronx              Woodlawn            Deli / Bodega   
8            Bronx               Norwood              Pizza Place   
10           Bronx            Baychester               Donut Shop   
11           Bronx        Pelham Parkway              Bus Station   
13           Bronx          Bedford Park                    Diner   
14           Bronx    University Heights              Pizza Place   
15           Bronx        Morris Heights            Grocery Store   
16           Bronx               Fordham        Mobile Phone Shop   
17           Bronx          East Tremont              Pizza Place   
20           Bronx               Melrose              Pizza Place   
21           Bronx            Mott Haven       Chinese Restaurant   
24           Bronx           Hunts Point                     Café   
28           Bronx           Throgs Neck              Coffee Shop   
30           Bronx           Parkchester              Supermarket   
31           Bronx    Westchester Square     Fast Food Restaurant   
32           Bronx              Van Nest            Deli / Bodega   
33           Bronx           Morris Park              Pizza Place   
34           Bronx               Belmont       Italian Restaurant   
36           Bronx       North Riverdale              Pizza Place   
38           Bronx         Schuylerville              Pizza Place   
40           Bronx           Castle Hill              Pizza Place   
42           Bronx        Pelham Gardens              Bus Station   
48        Brooklyn           Sunset Park                     Bank   
50        Brooklyn             Gravesend                   Bakery   
53        Brooklyn     Manhattan Terrace           Ice Cream Shop   
54        Brooklyn              Flatbush            Deli / Bodega   
55        Brooklyn         Crown Heights              Pizza Place   
80        Brooklyn          Borough Park                     Bank   
83        Brooklyn           Marine Park            Deli / Bodega   
90        Brooklyn             City Line               Donut Shop   
92        Brooklyn               Midwood              Pizza Place   
94        Brooklyn            Georgetown                     Bank   
98        Brooklyn         Ocean Parkway              Pizza Place   
103      Manhattan      Hamilton Heights              Pizza Place   
134         Queens                Corona              Supermarket   
137         Queens         Richmond Hill                   Lounge   
140         Queens             Sunnyside              Pizza Place   
142         Queens               Maspeth                    Diner   
143         Queens             Ridgewood                   Bakery   
144         Queens              Glendale            Deli / Bodega   
146         Queens             Woodhaven            Deli / Bodega   
147         Queens            Ozone Park                 Pharmacy   
149         Queens         College Point            Deli / Bodega   
154         Queens            Douglaston       Chinese Restaurant   
155         Queens             Glen Oaks                 Pharmacy   
156         Queens             Bellerose            Deli / Bodega   
157         Queens     Kew Gardens Hills                     Bank   
160         Queens        Jamaica Center        Mobile Phone Shop   
161         Queens       Oakland Gardens        Korean Restaurant   
162         Queens        Queens Village                     Bank   
170         Queens          Far Rockaway            Deli / Bodega   
171         Queens         Broad Channel            Deli / Bodega   
174         Queens            Beechhurst       Chinese Restaurant   
181         Queens           Floral Park       Salon / Barbershop   
184         Queens       Queensboro Hill       Chinese Restaurant   
187      

In [29]:
ny_merged.loc[ny_merged['Cluster Labels'] == 4, ny_merged.columns[[0,1] + list(range(5, ny_merged.shape[1]))]]

Borough Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
192         Queens    Somerville                  Park           Yoga Studio   
203  Staten Island     Todt Hill                  Park           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
192               Exhibit               Factory    Falafel Restaurant   
203               Exhibit               Factory    Falafel Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
192                  Farm        Farmers Market  Fast Food Restaurant   
203                  Farm        Farmers Market  Fast Food Restaurant   

    9th Most Common Venue 10th Most Common Venue  
192                 Field    Filipino Restaurant  
203                 Field    Filipino Restaurant

In [30]:
ny_merged.loc[ny_merged['Cluster Labels'] == 5, ny_merged.columns[[0,1] + list(range(5, ny_merged.shape[1]))]]

Borough   Neighbourhood 1st Most Common Venue  \
85        Brooklyn        Sea Gate           Bus Station   
172         Queens    Breezy Point                 Beach   
178         Queens  Rockaway Beach                 Beach   
179         Queens        Neponsit                 Beach   
190         Queens    Belle Harbor                 Beach   
191         Queens   Rockaway Park                 Beach   
232  Staten Island   Midland Beach                 Beach   
288         Queens         Roxbury          Neighborhood   
302         Queens         Hammels                 Beach   

         2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
85                 Sports Club                 Beach   American Restaurant   
172        Monument / Landmark                 Trail              Bus Stop   
178  Latin American Restaurant        Ice Cream Shop    Seafood Restaurant   
179                Yoga Studio                  Food    Falafel Restaurant   
190              Deli / Bodega                   Pub                   Spa   
191                 Donut Shop           Pizza Place            Steakhouse   
232              Deli / Bodega            Restaurant        Baseball Field   
288                  Irish Pub                 Beach                 Trail   
302              Deli / Bodega              Bus Stop            Food Truck   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
85           Home Service                   Spa           Yoga Studio   
172           Yoga Studio                  Farm        Farmers Market   
178             BBQ Joint      Arepa Restaurant           Pizza Place   
179                  Farm        Farmers Market  Fast Food Restaurant   
190            Donut Shop              Boutique    Italian Restaurant   
191          Liquor Store            Smoke Shop            Bagel Shop   
232             Pet Store    Chinese Restaurant          Liquor Store   
288  Fast Food Restaurant        Baseball Field         Deli / Bodega   
302               Dog Run  Gym / Fitness Center            Shoe Store   

       8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
85               Flea Market    Falafel Restaurant                   Farm  
172     Fast Food Restaurant                 Field    Filipino Restaurant  
178       Chinese Restaurant            Bagel Shop                    Bar  
179                    Field   Filipino Restaurant      Fish & Chips Shop  
190       Mexican Restaurant    Chinese Restaurant             Bagel Shop  
191       Chinese Restaurant                  Bank                    Bar  
232                Bookstore    Russian Restaurant               Bus Stop  
288  Fruit & Vegetable Store    Frozen Yogurt Shop                Factory  
302      Fried Chicken Joint                 Diner            Bus Station

In [31]:
ny_merged.loc[ny_merged['Cluster Labels'] == 6, ny_merged.columns[[0,1] + list(range(5, ny_merged.shape[1]))]]

Borough Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
303  Queens     Bayswater            Playground           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
303           Flea Market            Eye Doctor               Factory   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
303    Falafel Restaurant                  Farm        Farmers Market   

    9th Most Common Venue 10th Most Common Venue  
303  Fast Food Restaurant                  Field

In [32]:
ny_merged.loc[ny_merged['Cluster Labels'] == 7, ny_merged.columns[[0,1] + list(range(5, ny_merged.shape[1]))]]

Borough Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
207  Staten Island    Port Ivory                   Bar                  Food   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
207               Factory    Falafel Restaurant                  Farm   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
207        Farmers Market  Fast Food Restaurant                 Field   

    9th Most Common Venue 10th Most Common Venue  
207   Filipino Restaurant      Fish & Chips Shop

In [39]:
ny_merged.loc[ny_merged['Cluster Labels'] == 8, ny_merged.columns[[0,1] + list(range(5, ny_merged.shape[1]))]]

Borough Neighbourhood 1st Most Common Venue 2nd Most Common Venue  \
257  Staten Island  Howland Hook         Boat or Ferry           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
257     Food & Drink Shop    Falafel Restaurant                  Farm   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
257        Farmers Market  Fast Food Restaurant                 Field   

    9th Most Common Venue 10th Most Common Venue  
257   Filipino Restaurant      Fish & Chips Shop

In [40]:
ny_merged.loc[ny_merged['Cluster Labels'] == 9, ny_merged.columns[[0,1] + list(range(5, ny_merged.shape[1]))]]

Borough              Neighbourhood      1st Most Common Venue  \
3            Bronx                  Fieldston       Medical Supply Store   
4            Bronx                  Riverdale                       Park   
12           Bronx                City Island                       Park   
22           Bronx                Port Morris     Furniture / Home Store   
27           Bronx               Clason Point                       Park   
29           Bronx               Country Club             Sandwich Place   
35           Bronx             Spuyten Duyvil                       Park   
37           Bronx                 Pelham Bay         Italian Restaurant   
39           Bronx             Edgewater Park         Italian Restaurant   
46        Brooklyn                  Bay Ridge         Italian Restaurant   
47        Brooklyn                Bensonhurst         Chinese Restaurant   
49        Brooklyn                 Greenpoint                        Bar   
51        Brooklyn             Brighton Beach         Russian Restaurant   
52        Brooklyn             Sheepshead Bay         Turkish Restaurant   
57        Brooklyn                 Kensington            Thai Restaurant   
58        Brooklyn            Windsor Terrace                      Plaza   
59        Brooklyn           Prospect Heights                        Bar   
60        Brooklyn                Brownsville        Fried Chicken Joint   
61        Brooklyn               Williamsburg                Coffee Shop   
62        Brooklyn                   Bushwick                        Bar   
63        Brooklyn         Bedford Stuyvesant                Coffee Shop   
64        Brooklyn           Brooklyn Heights              Deli / Bodega   
65        Brooklyn                Cobble Hill                Pizza Place   
66        Brooklyn            Carroll Gardens         Italian Restaurant   
67        Brooklyn                   Red Hook         Seafood Restaurant   
68        Brooklyn                    Gowanus                        Bar   
69        Brooklyn                Fort Greene         Italian Restaurant   
70        Brooklyn                 Park Slope                Coffee Shop   
77        Brooklyn            Manhattan Beach                       Café   
78        Brooklyn               Coney Island           Baseball Stadium   
79        Brooklyn                 Bath Beach               Dessert Shop   
81        Brooklyn              Dyker Heights               Burger Joint   
82        Brooklyn            Gerritsen Beach             Ice Cream Shop   
84        Brooklyn               Clinton Hill         Italian Restaurant   
86        Brooklyn                   Downtown               Burger Joint   
87        Brooklyn                Boerum Hill               Dance Studio   
88        Brooklyn  Prospect Lefferts Gardens                       Café   
91        Brooklyn               Bergen Beach            Harbor / Marina   
95        Brooklyn          East Williamsburg              Deli / Bodega   
96        Brooklyn                 North Side                Coffee Shop   
97        Brooklyn                 South Side                        Bar   
99        Brooklyn              Fort Hamilton                Pizza Place   
100      Manhattan                  Chinatown         Chinese Restaurant   
101      Manhattan         Washington Heights                       Café   
102      Manhattan                     Inwood         Mexican Restaurant   
104      Manhattan             Manhattanville         Seafood Restaurant   
105      Manhattan             Central Harlem         African Restaurant   
106      Manhattan                East Harlem         Mexican Restaurant   
107      Manhattan            Upper East Side                    Exhibit   
108      Manhattan                  Yorkville         Italian Restaurant   
109      Manhattan                 Lenox Hill           Sushi Restaurant   
110      Manhattan           Roosevelt Island              

In [68]:
df1 = ny_merged.loc[ny_merged['Cluster Labels'] == 2, ny_merged.columns[[0,1] + list(range(5, ny_merged.shape[1]))]]

In [69]:
df1.shape

(2, 12)

# Determine Population Density in Boroughs

## Analyze Population of Boroughs

In [37]:
#Determine the Boroughs Locations
address = 'Bronx, NY'
geolocator = Nominatim(user_agent="ny_explorer")
location1 = geolocator.geocode(address)
latitude1 = location1.latitude
longitude1 = location1.longitude

address2 = 'Brooklyn, NY'
geolocator2 = Nominatim(user_agent="ny_explorer")
location2 = geolocator2.geocode(address2)
latitude2 = location2.latitude
longitude2 = location2.longitude

address3 = 'Queens, NY'
geolocator3 = Nominatim(user_agent="ny_explorer")
location3 = geolocator3.geocode(address3)
latitude3 = location3.latitude
longitude3 = location3.longitude

address4 = 'Manhattan, NY'
geolocator4 = Nominatim(user_agent="ny_explorer")
location4 = geolocator4.geocode(address4)
latitude4 = location4.latitude
longitude4 = location4.longitude

address5 = 'Staten Island, NY'
geolocator5 = Nominatim(user_agent="ny_explorer")
location5 = geolocator5.geocode(address5)
latitude5 = location5.latitude
longitude5 = location5.longitude

print('The geograpical coordinates of the Bronx is {}, {}.'.format(latitude1, longitude1))
print('The geograpical coordinates of Brooklyn is {}, {}.'.format(latitude2, longitude2))
print('The geograpical coordinates of Queens is {}, {}.'.format(latitude3, longitude3))
print('The geograpical coordinates of Manhattan is {}, {}.'.format(latitude4, longitude4))
print('The geograpical coordinates of Staten Island  is {}, {}.'.format(latitude5, longitude5))

The geograpical coordinates of the Bronx is 40.8466508, -73.8785937.
The geograpical coordinates of Brooklyn is 40.6501024, -73.9495829.
The geograpical coordinates of Queens is 40.7498243, -73.7976337.
The geograpical coordinates of Manhattan is 40.7896239, -73.9598939.
The geograpical coordinates of Staten Island  is 40.5834557, -74.1496048.


#### Population Data for New York City drawn from the "New York city Population Projections by Age/Sex & Borough, 2010-2040 Report conducted by the City of New York (https://www1.nyc.gov/assets/planning/download/pdf/planning-level/nyc-population/projections_report_2010_2040.pdf).  This lists the projected New York City Population by borough in 2030. 

In [38]:
#Develop the Boroughs Locations and Populations
population_data = {'Borough': ['Bronx', 'Brooklyn', 'Queens', 'Manhattan', 'Staten Island'],
                  'Population - 2020': [1446788, 2648452, 1638281, 2330295, 487155],
                   'Population - 2030': [1518998, 2754009, 1676720, 2373551, 49749],
                  'Latitude': [40.8466508, 40.6501038, 40.7498243, 40.7896239, 40.5834557],
                  'Longitude': [-73.8785937, -73.9495823,-73.7976337, -73.9598939, -74.1496048]}
pop_data_df=pd.DataFrame(population_data, columns = ['Borough', 'Population - 2020', 'Population - 2030', 'Latitude', 'Longitude'])
print(pop_data_df)

         Borough  Population - 2020  Population - 2030   Latitude  Longitude
0          Bronx            1446788            1518998  40.846651 -73.878594
1       Brooklyn            2648452            2754009  40.650104 -73.949582
2         Queens            1638281            1676720  40.749824 -73.797634
3      Manhattan            2330295            2373551  40.789624 -73.959894
4  Staten Island             487155              49749  40.583456 -74.149605
